In [6]:
import json
from owlready2 import get_ontology, Thing, DataProperty, ObjectProperty, FunctionalProperty
from unidecode import unidecode

# Charger les données JSON
with open('pokemons.json', 'r', encoding='utf-8') as file:
    pokemons_data = json.load(file)

# Créer une nouvelle ontologie
onto = get_ontology("http://example.org/onto/pokemon")

with onto:
    class Pokemon(Thing):
        pass

    class Type(Thing):
        pass
    
    class Stat(Thing):
        pass
    
    class Sensi(Thing):
        pass

    class hasType(ObjectProperty):
        domain = [Pokemon]
        range = [Type]
    
    class hasStat(ObjectProperty):
        domain = [Pokemon]
        range = [Stat]
        
    class hasSensi(ObjectProperty):
        domain = [Pokemon]
        range = [Sensi]
        
    class sensiType(ObjectProperty):
        domain = [Sensi]
        range = [Type]

    class nom(DataProperty, FunctionalProperty):
        domain = [Pokemon, Type, Stat, Sensi]
        range = [str]
    
    class valeur(DataProperty, FunctionalProperty): 
        domain = [Stat]
        range = [int]

    class valeurfloat(DataProperty, FunctionalProperty):
        domain = [Sensi]
        range = [float]

    types = {}

    for pokemon_data in pokemons_data:
        # Types du Pokémon
        types_instances = []
        for type_name in pokemon_data['types']:
            type_name = unidecode(type_name)
            if type_name not in types:
                types[type_name] = Type(nom=type_name)
            types_instances.append(types[type_name])
        
        pokemon_nom = unidecode(pokemon_data['nom']) 
        pokemon_instance = Pokemon(nom=pokemon_nom)
        
        # Association des types au Pokémon
        for type_instance in types_instances:
            pokemon_instance.hasType.append(type_instance)
        
        # Statistiques du Pokémon
        for stat_name, stat_value in pokemon_data['stats'].items():
            stat_name = unidecode(stat_name)  
            stat_instance = Stat(nom=stat_name, valeur=stat_value)
            pokemon_instance.hasStat.append(stat_instance)
            
        # Sensibilités du Pokémon
        for sensibilite_name, sensibilite_value in pokemon_data['sensibilities'].items():
            type_instance = types.get(unidecode(sensibilite_name), Type(nom=unidecode(sensibilite_name)))
            sensibilite_instance = Sensi(nom=unidecode(sensibilite_name), valeurfloat=sensibilite_value)
            sensibilite_instance.sensiType.append(type_instance)
            pokemon_instance.hasSensi.append(sensibilite_instance)

onto.save(file="pokemon_ontology.owl", format="rdfxml")

print("Ontologie créée et sauvegardée avec les données JSON.")


Ontologie créée et sauvegardée avec les données JSON.


In [7]:
import json
from owlready2 import get_ontology, sync_reasoner, default_world

# Charger l'ontologie à partir du fichier sauvegardé
onto_path = "./pokemon_ontology.owl" 
onto = get_ontology(onto_path).load()

# Utiliser un moteur de raisonnement pour inférer de nouvelles connaissances
sync_reasoner()


* Owlready2 * Running HermiT...
    java -Xmx2000M -cp c:\Users\basti\AppData\Local\Programs\Python\Python310\lib\site-packages\owlready2\hermit;c:\Users\basti\AppData\Local\Programs\Python\Python310\lib\site-packages\owlready2\hermit\HermiT.jar org.semanticweb.HermiT.cli.CommandLine -c -O -D -I file:///C:/Users/basti/AppData/Local/Temp/tmp5leuah0q
* Owlready2 * HermiT took 14.09266996383667 seconds
* Owlready * Reparenting pokemon.type5550: {pokemon.Type} => {pokemon.Pokemon, pokemon.Sensi, pokemon.Type, pokemon.Stat}
* Owlready * Reparenting pokemon.pokemon1928: {pokemon.Pokemon} => {pokemon.Pokemon, pokemon.Sensi, pokemon.Type, pokemon.Stat}
* Owlready * Reparenting pokemon.type5551: {pokemon.Type} => {pokemon.Pokemon, pokemon.Sensi, pokemon.Type, pokemon.Stat}
* Owlready * Reparenting pokemon.pokemon1929: {pokemon.Pokemon} => {pokemon.Pokemon, pokemon.Sensi, pokemon.Type, pokemon.Stat}
* Owlready * Reparenting pokemon.type5552: {pokemon.Type} => {pokemon.Pokemon, pokemon.Sensi, pok

In [10]:
query = """
PREFIX rdf: <http://www.w3.org/1999/02/22-rdf-syntax-ns#>
PREFIX onto: <http://example.org/onto/pokemon#>
SELECT DISTINCT ?pokemon WHERE {
    ?pokemon rdf:type onto:Pokemon .
    ?pokemon onto:hasType ?type .
    ?type onto:nom "Feu" .
}
"""

results = list(default_world.sparql(query))

for result in results:
    print(f"Pokémon de type Feu : {result[0].nom}")


Pokémon de type Feu : Salameche
Pokémon de type Feu : Reptincel
Pokémon de type Feu : Dracaufeu
Pokémon de type Feu : Goupix
Pokémon de type Feu : Feunard
Pokémon de type Feu : Caninos
Pokémon de type Feu : Arcanin
Pokémon de type Feu : Hericendre
Pokémon de type Feu : Feurisson
Pokémon de type Feu : Typhlosion
Pokémon de type Feu : Ponyta
Pokémon de type Feu : Galopa
Pokémon de type Feu : Ouisticram
Pokémon de type Feu : Chimpenfeu
Pokémon de type Feu : Simiabraz
Pokémon de type Feu : Poussifeu
Pokémon de type Feu : Galifeu
Pokémon de type Feu : Brasegali
Pokémon de type Feu : Magmar
Pokémon de type Feu : Limagma
Pokémon de type Feu : Volcaropod
Pokémon de type Feu : Pyroli
Pokémon de type Feu : Malosse
Pokémon de type Feu : Demolosse
Pokémon de type Feu : Sulfura
Pokémon de type Feu : Magby
Pokémon de type Feu : Entei
Pokémon de type Feu : Maganon
Pokémon de type Feu : Ho-Oh
Pokémon de type Feu : Heatran
Pokémon de type Feu : Chamallot
Pokémon de type Feu : Camerupt
Pokémon de type F

In [35]:
query = """
PREFIX rdf: <http://www.w3.org/1999/02/22-rdf-syntax-ns#>
PREFIX onto: <http://example.org/onto/pokemon#>
SELECT DISTINCT ?otherPokemon WHERE {
    ?reptincel onto:nom "Reptincel" .
    ?reptincel onto:hasType ?reptincelType .
    ?sensi onto:sensiType ?reptincelType .
    ?sensi onto:valeurfloat ?value .
    FILTER(?value >= 4) .
    ?otherPokemon onto:hasSensi ?sensi .
}
"""

# Exécution de la requête et récupération des résultats
results = list(default_world.sparql(query))

# Affichage des résultats
for result in results:
    pokemon = result[0]
    print(f"Pokémon sensible au type de Reptincel : {pokemon.nom}")


Pokémon sensible au type de Reptincel : Paras
Pokémon sensible au type de Reptincel : Parasect
Pokémon sensible au type de Reptincel : Cheniselle
Pokémon sensible au type de Reptincel : Foretress
Pokémon sensible au type de Reptincel : Cizayox
Pokémon sensible au type de Reptincel : Blizzi
Pokémon sensible au type de Reptincel : Blizzaroi
Pokémon sensible au type de Reptincel : Paras
Pokémon sensible au type de Reptincel : Parasect
Pokémon sensible au type de Reptincel : Cheniselle
Pokémon sensible au type de Reptincel : Foretress
Pokémon sensible au type de Reptincel : Cizayox
Pokémon sensible au type de Reptincel : Blizzi
Pokémon sensible au type de Reptincel : Blizzaroi


In [33]:
def text_to_sparql(text_query):
    if "type feu" in text_query.lower():
        return """
        PREFIX rdf: <http://www.w3.org/1999/02/22-rdf-syntax-ns#>
        PREFIX onto: <http://example.org/onto/pokemon#>
        SELECT DISTINCT ?pokemon WHERE {
            ?pokemon rdf:type onto:Pokemon .
            ?pokemon onto:hasType ?type .
            ?type onto:nom "Feu" .
        }
        """
    return None

query_text = "Quels sont les type feu ?"

sparql_query = text_to_sparql(query_text)

if sparql_query :    
    results = list(default_world.sparql(sparql_query))
    for result in results:
        print(f"Pokémon de type Feu : {result[0].nom}")


Pokémon de type Feu : Salameche
Pokémon de type Feu : Reptincel
Pokémon de type Feu : Dracaufeu
Pokémon de type Feu : Goupix
Pokémon de type Feu : Feunard
Pokémon de type Feu : Caninos
Pokémon de type Feu : Arcanin
Pokémon de type Feu : Hericendre
Pokémon de type Feu : Feurisson
Pokémon de type Feu : Typhlosion
Pokémon de type Feu : Ponyta
Pokémon de type Feu : Galopa
Pokémon de type Feu : Ouisticram
Pokémon de type Feu : Chimpenfeu
Pokémon de type Feu : Simiabraz
Pokémon de type Feu : Poussifeu
Pokémon de type Feu : Galifeu
Pokémon de type Feu : Brasegali
Pokémon de type Feu : Magmar
Pokémon de type Feu : Limagma
Pokémon de type Feu : Volcaropod
Pokémon de type Feu : Pyroli
Pokémon de type Feu : Malosse
Pokémon de type Feu : Demolosse
Pokémon de type Feu : Sulfura
Pokémon de type Feu : Magby
Pokémon de type Feu : Entei
Pokémon de type Feu : Maganon
Pokémon de type Feu : Ho-Oh
Pokémon de type Feu : Heatran
Pokémon de type Feu : Chamallot
Pokémon de type Feu : Camerupt
Pokémon de type F